# _*Applied Data Science Capstone*_: The Battle of the Neighbourhoods
## _Author_: Kishan Y Narotam

# Introduction
A venture capitalist is known as a private equity investor who seeks opportunity in high-growth potential companies such as small businesses and startups in exchange for a stake in the respective company. The risk-reward factor of investing in these companies can be drastic, and if invested correctly can yield a substantial return for the investor. Venture capital firms began in the United States in the early to mid-1900s and has continued to grow exponentially as the world evolved through the Dot-Com burst and into the Fourth Industrial Revolution [1](https://www.investopedia.com/terms/v/venturecapitalist.asp#:~:text=A%20venture%20capitalist%20(VC)%20is,have%20access%20to%20equities%20markets).<br>

The popular television show _Shark Tank_ and its respective spinoff such as _Dragon’s Den_ in the UK has brought to life the way investors, specifically venture capitalists invest their money in small businesses and startups. In order to mitigate the risks, investors must know about the business and what the plan would be to succeed.<br>

This project aims to provide information to venture capitalists on what businesses are popular based on data about Toronto, Canada. The idea is to be able to make valid assumptions based on the popularity of certain venues in the various boroughs. The information gathered will allow venture capitalists to know what type of businesses are in high-demand as well as potential opportunities for less popular businesses. 10 neighbourhoods will be chosen to do a further in-depth analysis which includes population size and income of thei respective neighbourhoods.


# Data
Based on what we aim to achieve with this project, the data required includes:
 - List of postal codes, corresponding boroughs and neighbourhoods for the City of Toronto.
 - The demographics of the Toronto neighbourhoods.
 - The various venues such as restaurants, bars, coffee shops, malls, etc. around each of the neighbourhoods.
 - The longitude and latitude of each neighbourhood and venues.
 
## Data Sources
The list of postal codes, boroughs and neighbourhoods are retrieved from a Wikipedia table listing all of the postal codes in Canada that begin with the letter M. This was chosen as the postal codes that begin with the letter M are the boroughs and neighbourhoods that are found within the city of Toronto. The original table is found at the link below:<br>
[Neighbourhoods and Postal Codes](https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M).<br>
This postal code data along with the corresponding boroughs and neighbourhoods will correlate directly with the geospatial data file. This data file provides the longitude and latitude of each postal code that is stored in a \textit{csv} file. The link to the file can be found at the link below:<br>
[Geospatial Data](http://cocl.us/Geospatial_data).<br>
The demographics data is taken from the Toronto Open Data Catalogue, relating to neighbourhood profiles. The csv file consists of the neighbourhood profiles from a census done in 2016, which includes population distribution across various races and religions, languages spoken, immigration and citizenship, education and finances. This file is provided as a \textit{csv} file and can be found at the link below:<br>
[Demographics Data](https://ckan0.cf.opendata.inter.prod-toronto.ca/download_resource/ef0239b1-832b-4d0b-a1f3-4153e53b189e?format=csv)<br>
These above links alongside the Foursquare API will be used to map the neighbourhoods and retrieve the data relating to the various venues. For this project, due to the limitations of the free account on Foursquare, the search limit of the venues is set to 100 with a radius of 500 metres of each neighbourhood.


## Methodology

## Importing the Libraries

In [1]:
# Installing the necessary libraries that will be required for the project
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!pip install geopy
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

# BeautifulSoup for extracting data from HTML page
from bs4 import BeautifulSoup

print('Libraries imported.')

     |████████████████████████████████| 94 kB 5.6 MB/s  eta 0:00:01
Libraries imported.


## Importing the Data Sources

### Toronto Neighbourhoods Data
#### Scraping the postal code and neighbourhood data from Wikipedia

In [2]:
wiki = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
# using BeautifulSoup, we can pull the table from the webpage
soup = BeautifulSoup(wiki, 'lxml')
# using the prettify, we obtain the pure raw html text
table = str(soup.table)

#### Converting the HTML table into a dataframe

In [3]:
# read_html returns a list of dataframes, and so we take the entire list and combine it into a single dataframe.
dfs = pd.read_html(table)
df = dfs[0]
df.head()

Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

#### Preprocessing

In [4]:
# Dropping rows where Borough has a "Not assigned"
df = df[df.Borough != 'Not assigned'].reset_index(drop=True)
df.head()

Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [5]:
# Filling in all 'Not Assigned' Neighbourhoods with the Borough
# using the where from Numpy is a shorter version of using an if statement
df['Neighbourhood'] = np.where(df['Neighbourhood'] == 'Not assigned', df['Borough'], df['Neighbourhood'])
df.head(20)

Postal Code           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   
12         M1C       Scarborough   
13         M3C        North York   
14         M4C         East York   
15         M5C  Downtown Toronto   
16         M6C              York   
17         M9C         Etobicoke   
18         M1E       Scarborough   
19         M4E      East Toronto   

                                        Neighbourhood  
0                                           Parkwoods  
1                                    Victoria Village  
2                           Regent Park, Harbourfront  
3                    Lawrence Manor, Lawrence Heights  
4         Queen's Park, Ontario Provincial Government  
5             Islington Avenue, Humber Valley Village  
6                                      Malvern, Rouge  
7                                           Don Mills  
8                     Parkview Hill, Woodbine Gardens  
9                            Garden District, Ryerson  
10                                          Glencairn  
11  West Deane Park, Princess Gardens, Martin Grov...  
12             Rouge Hill, Port Union, Highland Creek  
13                                          Don Mills  
14                                   Woodbine Heights  
15                                     St. James Town  
16                                 Humewood-Cedarvale  
17  Eringate, Bloordale Gardens, Old Burnhamthorpe...  
18                  Guildwood, Morningside, West Hill  
19                                        The Beaches

### Geospatial Data

In [6]:
coord = pd.read_csv('http://cocl.us/Geospatial_data')
coord.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [7]:
# similar to that in SQL, we will use a left join on the Postal Code column
torontodf = df.merge(coord, on ='Postal Code', how='left')
torontodf.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

### Demographics Data (for in-depth analysis)

The data necessary from this csv file is two rows which contain:
- The population of the neighbourhoods in 2016 (which is _id = 3)
- The average income of each neighbourhood (which is _id = 2273)

In [8]:
# using the read_csv function to read in the csv file
demodf = pd.read_csv('https://ckan0.cf.opendata.inter.prod-toronto.ca/download_resource/ef0239b1-832b-4d0b-a1f3-4153e53b189e?format=csv')
demodf.head()

_id                   Category                      Topic  \
0    1  Neighbourhood Information  Neighbourhood Information   
1    2  Neighbourhood Information  Neighbourhood Information   
2    3                 Population   Population and dwellings   
3    4                 Population   Population and dwellings   
4    5                 Population   Population and dwellings   

                      Data Source               Characteristic  \
0                 City of Toronto         Neighbourhood Number   
1                 City of Toronto         TSNS2020 Designation   
2  Census Profile 98-316-X2016001             Population, 2016   
3  Census Profile 98-316-X2016001             Population, 2011   
4  Census Profile 98-316-X2016001  Population Change 2011-2016   

  City of Toronto Agincourt North Agincourt South-Malvern West  \
0             NaN             129                          128   
1             NaN  No Designation               No Designation   
2       2,731,571          29,113                       23,757   
3       2,615,060          30,279                       21,988   
4           4.50%          -3.90%                        8.00%   

        Alderwood           Annex Banbury-Don Mills  Bathurst Manor  \
0              20              95                42              34   
1  No Designation  No Designation    No Designation  No Designation   
2          12,054          30,526            27,695          15,873   
3          11,904          29,177            26,918          15,434   
4           1.30%           4.60%             2.90%           2.80%   

  Bay Street Corridor Bayview Village Bayview Woods-Steeles  \
0                  76              52                    49   
1      No Designation  No Designation        No Designation   
2              25,797          21,396                13,154   
3              19,348          17,671                13,530   
4              33.30%          21.10%                -2.80%   

  Bedford Park-Nortown Beechborough-Greenbrook         Bendale  \
0                   39                     112             127   
1       No Designation                     NIA  No Designation   
2               23,236                   6,577          29,960   
3               23,185                   6,488          27,876   
4                0.20%                   1.40%           7.50%   

  Birchcliffe-Cliffside Black Creek     Blake-Jones Briar Hill-Belgravia  \
0                   122          24              69                  108   
1        No Designation         NIA  No Designation       No Designation   
2                22,291      21,737           7,727               14,257   
3                21,856      22,057           7,763               14,302   
4                 2.00%      -1.50%          -0.50%               -0.30%   

  Bridle Path-Sunnybrook-York Mills Broadview North Brookhaven-Amesbury  \
0                                41              57                  30   
1                    No Designation  No Designation      No Designation   
2                             9,266          11,499              17,757   
3                             8,713          11,563              17,787   
4                             6.30%          -0.60%              -0.20%   

  Cabbagetown-South St. James Town Caledonia-Fairbank       Casa Loma  \
0                               71                109              96   
1                   No Designation     No Designation  No Designation   
2                           11,669              9,955          10,968   
3                           12,053              9,851          10,487   
4                           -3.20%              1.10%           4.60%   

  Centennial Scarborough Church-Yonge Corridor Clairlea-Birchmount  \
0                    133                    75                 120   
1         No Designation        No Designation      No Designation   
2                 13,362                31,340              26,9

In [9]:
# drop the first 6 columns
demodf.drop(columns=['_id', 'Category','Topic', 'Data Source', 'Characteristic', 'City of Toronto'], inplace=True)
demodf.head()

Agincourt North Agincourt South-Malvern West       Alderwood  \
0             129                          128              20   
1  No Designation               No Designation  No Designation   
2          29,113                       23,757          12,054   
3          30,279                       21,988          11,904   
4          -3.90%                        8.00%           1.30%   

            Annex Banbury-Don Mills  Bathurst Manor Bay Street Corridor  \
0              95                42              34                  76   
1  No Designation    No Designation  No Designation      No Designation   
2          30,526            27,695          15,873              25,797   
3          29,177            26,918          15,434              19,348   
4           4.60%             2.90%           2.80%              33.30%   

  Bayview Village Bayview Woods-Steeles Bedford Park-Nortown  \
0              52                    49                   39   
1  No Designation        No Designation       No Designation   
2          21,396                13,154               23,236   
3          17,671                13,530               23,185   
4          21.10%                -2.80%                0.20%   

  Beechborough-Greenbrook         Bendale Birchcliffe-Cliffside Black Creek  \
0                     112             127                   122          24   
1                     NIA  No Designation        No Designation         NIA   
2                   6,577          29,960                22,291      21,737   
3                   6,488          27,876                21,856      22,057   
4                   1.40%           7.50%                 2.00%      -1.50%   

      Blake-Jones Briar Hill-Belgravia Bridle Path-Sunnybrook-York Mills  \
0              69                  108                                41   
1  No Designation       No Designation                    No Designation   
2           7,727               14,257                             9,266   
3           7,763               14,302                             8,713   
4          -0.50%               -0.30%                             6.30%   

  Broadview North Brookhaven-Amesbury Cabbagetown-South St. James Town  \
0              57                  30                               71   
1  No Designation      No Designation                   No Designation   
2          11,499              17,757                           11,669   
3          11,563              17,787                           12,053   
4          -0.60%              -0.20%                           -3.20%   

  Caledonia-Fairbank       Casa Loma Centennial Scarborough  \
0                109              96                    133   
1     No Designation  No Designation         No Designation   
2              9,955          10,968                 13,362   
3              9,851          10,487                 13,093   
4              1.10%           4.60%                  2.10%   

  Church-Yonge Corridor Clairlea-Birchmount    Clanton Park      Cliffcrest  \
0                    75                 120              33             123   
1        No Designation      No Designation  No Designation  No Designation   
2                31,340              26,984          16,472          15,935   
3                28,349              24,770          14,612          15,703   
4                10.60%               8.90%          12.70%           1.50%   

  Corso Italia-Davenport        Danforth Danforth East York  \
0                     92              66                 59   
1         No Designation  No Designation     No Designation   
2                 14,133           9,666             17,180   
3                 13,743           9,444             16,712   
4                  2.80%           2.40%              2.80%   

  Don Valley Village             Dorset Park  \
0                 47                     126   
1     No Designation  Emerging Neighbourhood   
2             2

In [10]:
# retrieving the population record
pop = demodf.loc[2,:]
popdf = pd.DataFrame()
popdf = popdf.append(pop)
popdf = popdf.transpose()
popdf.reset_index(level=0, inplace=True)
popdf.columns = ['Neighbourhood', 'Population']
popdf.head()

Neighbourhood Population
0               Agincourt North     29,113
1  Agincourt South-Malvern West     23,757
2                     Alderwood     12,054
3                         Annex     30,526
4             Banbury-Don Mills     27,695

In [11]:
# Merge the population table to the neighbourhood table
joinpopdf = torontodf.merge(popdf, on='Neighbourhood', how='left')
joinpopdf

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
5           M9A         Etobicoke   
6           M1B       Scarborough   
7           M3B        North York   
8           M4B         East York   
9           M5B  Downtown Toronto   
10          M6B        North York   
11          M9B         Etobicoke   
12          M1C       Scarborough   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
16          M6C              York   
17          M9C         Etobicoke   
18          M1E       Scarborough   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
21          M6E              York   
22          M1G       Scarborough   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
26          M1H       Scarborough   
27          M2H        North York   
28          M3H        North York   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
32          M1J       Scarborough   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
38          M1K       Scarborough   
39          M2K        North York   
40          M3K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
44          M1L       Scarborough   
45          M2L        North York   
46          M3L        North York   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
49          M6L        North York   
50          M9L        North York   
51          M1M       Scarborough   
52          M2M        North York   
53          M3M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
57          M9M        North York   
58          M1N       Scarborough   
59          M2N        North York   
60          M3N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
63          M6N              York   
64          M9N              York   
65          M1P       Scarborough   
66          M2P        North York   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
70          M9P         Etobicoke   
71          M1R       Scarborough   
72          M2R        North York   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
77          M9R         Etobicoke   
78          M1S       Scarborough   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
82          M1T       Scarborough   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
85          M1V       Scarborough   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
89          M9V         Etobicoke   
90          M1W       Scarborough   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
93          M8W         Etobicoke   
94          M9W         Etobicoke   
95          M1X       Scarborough   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
0                                            Parkwoods  43.753259 -79.32965

In [12]:
income = demodf.loc[2272,:]
incomedf = pd.DataFrame()
incomedf = incomedf.append(income)
incomedf = incomedf.transpose()
incomedf.reset_index(level=0, inplace=True)
incomedf.columns = ['Neighbourhood', 'Average Income']
incomedf.head()

Neighbourhood Average Income
0               Agincourt North         30,414
1  Agincourt South-Malvern West         31,825
2                     Alderwood         47,709
3                         Annex        112,766
4             Banbury-Don Mills         67,757

In [13]:
# Merge the income table to the neighbourhood table
indepthdf = joinpopdf.merge(incomedf, on='Neighbourhood', how='left')
indepthdf = indepthdf[indepthdf['Population'].notna()]
indepthdf.reset_index()

index Postal Code       Borough        Neighbourhood   Latitude  Longitude  \
0      1         M4A    North York     Victoria Village  43.725882 -79.315572   
1     16         M6C          York   Humewood-Cedarvale  43.693781 -79.428191   
2     19         M4E  East Toronto          The Beaches  43.676357 -79.293031   
3     22         M1G   Scarborough               Woburn  43.770992 -79.216917   
4     27         M2H    North York    Hillcrest Village  43.803762 -79.363452   
5     29         M4H     East York     Thorncliffe Park  43.705369 -79.349372   
6     32         M1J   Scarborough  Scarborough Village  43.744734 -79.239476   
7     39         M2K    North York      Bayview Village  43.786947 -79.385975   
8     50         M9L    North York        Humber Summit  43.756303 -79.565963   
9     64         M9N          York               Weston  43.706876 -79.518188   

  Population Average Income  
0     17,510         35,786  
1     14,365         65,274  
2     21,567         92,580  
3     53,485         30,878  
4     16,934         40,442  
5     21,108         28,875  
6     16,724         32,913  
7     21,396         52,035  
8     12,416         30,731  
9     17,992         32,997

## Creating our map

In [14]:
# Getting the coordinates of Toronto

address = 'Toronto, ON'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [15]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(torontodf['Latitude'], torontodf['Longitude'], torontodf['Borough'], torontodf['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

# Utilising Foursquare API

## Setting up Foursquare API

In [39]:
# During the analysis I have used my won credentials, however for security reasons, I have removed my ID and Secret values for final submission
CLIENT_ID = '' # 
CLIENT_SECRET = '' # 
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 
CLIENT_SECRET:


## Retrieving the top 100 venues within a 500 metre radius

Using the API the goal is to retrieve the following information:
- Venues
- Venue Latitude Values
- Venue Longitude Values
- Venue Categories

In [18]:
# Setting the radius of the search area
radius = 500

# create a blank array to store all the venues retrieved
venues_list=[]
for lat, lng, postcode, borough, neighbourhood in zip(torontodf['Latitude'], torontodf['Longitude'], torontodf['Postal Code'], torontodf['Borough'], torontodf['Neighbourhood']):

    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        lng, 
        radius, 
        LIMIT)

    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']

    # return only relevant information for each nearby venue
    venues_list.append([(
        postcode,
        borough,
        neighbourhood,
        lat, 
        lng, 
        v['venue']['name'], 
        v['venue']['location']['lat'], 
        v['venue']['location']['lng'],  
        v['venue']['categories'][0]['name']) for v in results])

# take the array and convert it to a dataframe with the corresponding information requested from the API
nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
nearby_venues.columns = ['Postal Code','Borough', 'Neighbourhood', 
              'Neighbourhood Latitude', 
              'Neighbourhood Longitude', 
              'Venue', 
              'Venue Latitude', 
              'Venue Longitude', 
              'Venue Category']

nearby_venues

Postal Code           Borough  \
0            M3A        North York   
1            M3A        North York   
2            M4A        North York   
3            M4A        North York   
4            M4A        North York   
5            M4A        North York   
6            M4A        North York   
7            M4A        North York   
8            M5A  Downtown Toronto   
9            M5A  Downtown Toronto   
10           M5A  Downtown Toronto   
11           M5A  Downtown Toronto   
12           M5A  Downtown Toronto   
13           M5A  Downtown Toronto   
14           M5A  Downtown Toronto   
15           M5A  Downtown Toronto   
16           M5A  Downtown Toronto   
17           M5A  Downtown Toronto   
18           M5A  Downtown Toronto   
19           M5A  Downtown Toronto   
20           M5A  Downtown Toronto   
21           M5A  Downtown Toronto   
22           M5A  Downtown Toronto   
23           M5A  Downtown Toronto   
24           M5A  Downtown Toronto   
25           M5A  Downtown Toronto   
26           M5A  Downtown Toronto   
27           M5A  Downtown Toronto   
28           M5A  Downtown Toronto   
29           M5A  Downtown Toronto   
30           M5A  Downtown Toronto   
31           M5A  Downtown Toronto   
32           M5A  Downtown Toronto   
33           M5A  Downtown Toronto   
34           M5A  Downtown Toronto   
35           M5A  Downtown Toronto   
36           M5A  Downtown Toronto   
37           M5A  Downtown Toronto   
38           M5A  Downtown Toronto   
39           M5A  Downtown Toronto   
40           M5A  Downtown Toronto   
41           M5A  Downtown Toronto   
42           M5A  Downtown Toronto   
43           M5A  Downtown Toronto   
44           M5A  Downtown Toronto   
45           M5A  Downtown Toronto   
46           M5A  Downtown Toronto   
47           M5A  Downtown Toronto   
48           M5A  Downtown Toronto   
49           M5A  Downtown Toronto   
50           M5A  Downtown Toronto   
51           M5A  Downtown Toronto   
52           M5A  Downtown Toronto   
53           M5A  Downtown Toronto   
54           M5A  Downtown Toronto   
55           M5A  Downtown Toronto   
56           M6A        North York   
57           M6A        North York   
58           M6A        North York   
59           M6A        North York   
60           M6A        North York   
61           M6A        North York   
62           M6A        North York   
63           M6A        North York   
64           M6A        North York   
65           M6A        North York   
66           M6A        North York   
67           M7A  Downtown Toronto   
68           M7A  Downtown Toronto   
69           M7A  Downtown Toronto   
70           M7A  Downtown Toronto   
71           M7A  Downtown Toronto   
72           M7A  Downtown Toronto   
73           M7A  Downtown Toronto   
74           M7A  Downtown Toronto   
75           M7A  Downtown Toronto   
76           M7A  Downtown Toronto   
77           M7A  Downtown Toronto   
78           M7A  Downtown Toronto   
79           M7A  Downtown Toronto   
80           M7A  Downtown Toronto   
81           M7A  Downtown Toronto   
82           M7A  Downtown Toronto   
83           M7A  Downtown Toronto   
84           M7A  Downtown Toronto   
85           M7A  Downtown Toronto   
86           M7A  Downtown Toronto   
87           M7A  Downtown Toronto   
88           M7A  Downtown Toronto   
89           M7A  Downtown Toronto   
90           M7A  Downtown Toronto   
91           M7A  Downtown Toronto   
92           M7A  Downtown Toronto   
93           M7A  Downtown Toronto   
94           M7A  Downtown Toronto   
95           M7A  Downtown Toronto   
96           M7A  Downtown Toronto   
97           M7A  Downtown Toronto   
98           M7A  Downtown Toronto   
99           M7A  Downtown Toronto   
100          M7A  Downtown Toronto   
101          M1B       Scarborough   
102          M3B        North York   
103          M3B        North York   
104          M3

In [19]:
# To get an understanding of the amount of data we requested and what was returned, we use the shape function
nearby_venues.shape

(2129, 9)

## Grouping the requested venues

In [20]:
# the idea is to gain an understanding of the number of venues requested and received for the neighbourhood
nearby_venues.groupby('Neighbourhood').count()

Postal Code  Borough  \
Neighbourhood                                                              
Agincourt                                                     5        5   
Alderwood, Long Branch                                        8        8   
Bathurst Manor, Wilson Heights, Downsview North              23       23   
Bayview Village                                               4        4   
Bedford Park, Lawrence Manor East                            24       24   
Berczy Park                                                  58       58   
Birch Cliff, Cliffside West                                   4        4   
Brockton, Parkdale Village, Exhibition Place                 23       23   
Business reply mail Processing Centre, South Ce...           17       17   
CN Tower, King and Spadina, Railway Lands, Harb...           14       14   
Caledonia-Fairbanks                                           4        4   
Canada Post Gateway Processing Centre                        14       14   
Cedarbrae                                                     8        8   
Central Bay Street                                           61       61   
Christie                                                     16       16   
Church and Wellesley                                         77       77   
Clarks Corners, Tam O'Shanter, Sullivan                      12       12   
Cliffside, Cliffcrest, Scarborough Village West               3        3   
Commerce Court, Victoria Hotel                              100      100   
Davisville                                                   33       33   
Davisville North                                              7        7   
Del Ray, Mount Dennis, Keelsdale and Silverthorn              6        6   
Don Mills                                                    24       24   
Dorset Park, Wexford Heights, Scarborough Town ...            8        8   
Downsview                                                    10       10   
Dufferin, Dovercourt Village                                 17       17   
East Toronto, Broadview North (Old East York)                 4        4   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...           10       10   
Fairview, Henry Farm, Oriole                                 66       66   
First Canadian Place, Underground city                      100      100   
Forest Hill North & West, Forest Hill Road Park               4        4   
Garden District, Ryerson                                    100      100   
Glencairn                                                     7        7   
Golden Mile, Clairlea, Oakridge                               8        8   
Guildwood, Morningside, West Hill                             8        8   
Harbourfront East, Union Station, Toronto Islands           100      100   
High Park, The Junction South                                24       24   
Hillcrest Village                                             6        6   
Humber Summit                                                 1        1   
Humberlea, Emery                                              1        1   
Humewood-Cedarvale                                            4        4   
India Bazaar, The Beaches West                               21       21   
Kennedy Park, Ionview, East Birchmount Park                   6        6   
Kensington Market, Chinatown, Grange Park                    65       65   
Kingsview Village, St. Phillips, Martin Grove G...            4        4   
Lawrence Manor, Lawrence Heights                             11       11   
Lawrence Park                                                 4        4   
Leaside                                                      32       32   
Little Portugal, Trinity                                     43       43   
Malvern, Rouge                                                1        1   
Milliken, Agincourt North, Steeles East, L'Amor...            3        3   
Mimico NW, The Queensway

In [21]:
# Identifying the number of unique categories
print('There are {} uniques categories.'.format(len(nearby_venues['Venue Category'].unique())))

There are 273 uniques categories.


## One Hot Encoding
We perform one hot encoding on the data as this will allow a machine learning model to be able to process the data.

In [22]:
# one hot encoding
toronto_onehot = pd.get_dummies(nearby_venues[['Venue Category']], prefix="", prefix_sep="")

toronto_onehot['Neighbourhood'] = nearby_venues['Neighbourhood'] 

fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head(10)

Neighbourhood  Accessories Store  Airport  Airport Food Court  \
0                  Parkwoods                  0        0                   0   
1                  Parkwoods                  0        0                   0   
2           Victoria Village                  0        0                   0   
3           Victoria Village                  0        0                   0   
4           Victoria Village                  0        0                   0   
5           Victoria Village                  0        0                   0   
6           Victoria Village                  0        0                   0   
7           Victoria Village                  0        0                   0   
8  Regent Park, Harbourfront                  0        0                   0   
9  Regent Park, Harbourfront                  0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   
5               0                0                 0                    0   
6               0                0                 0                    0   
7               0                0                 0                    0   
8               0                0                 0                    0   
9               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   
5             0         0            0           0                    0   
6             0         0            0           0                    0   
7             0         0            0           0                    0   
8             0         0            0           0                    0   
9             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0                 0                   0            0              0   
1                 0                   0            0              0   
2                 0                   0            0              0   
3                 0                   0            0              0   
4                 0                   0            0              0   
5                 0                   0            0              0   
6                 0                   0            0              0   
7                 0                   0            0              0   
8                 0                   0            0              0   
9                 0                   0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   
5          0           0           0       0     0    0               0   
6          0           0           0       0     0    0               0   
7          0           0           0       0     0    0               0   
8  

In [23]:
# Now we group the data and find the frequency (mean) of each venue occurrance
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.000000   
8   Business reply mail Processing Centre, South C...           0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
10                                Caledonia-Fairbanks           0.000000   
11              Canada Post Gateway Processing Centre           0.000000   
12                                          Cedarbrae           0.000000   
13                                 Central Bay Street           0.000000   
14                                           Christie           0.000000   
15                               Church and Wellesley           0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
18                     Commerce Court, Victoria Hotel           0.000000   
19                                         Davisville           0.000000   
20                                   Davisville North           0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
22                                          Don Mills           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.000000   
24                                          Downsview           0.000000   
25                       Dufferin, Dovercourt Village           0.000000   
26      East Toronto, Broadview North (Old East York)           0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
28                       Fairview, Henry Farm, Oriole           0.000000   
29             First Canadian Place, Underground city           0.000000   
30    Forest Hill North & West, Forest Hill Road Park           0.000000   
31                           Garden District, Ryerson           0.000000   
32                                          Glencairn           0.000000   
33                    Golden Mile, Clairlea, Oakridge           0.000000   
34                  Guildwood, Morningside, West Hill           0.000000   
35  Harbourfront East, Union Station, Toronto Islands           0.000000   
36                      High Park, The Junction South           0.000000   
37                                  Hillcrest Village           0.000000   
38                                      Humber Summit           0.000000   
39                                   Humberlea, Emery           0.000000   
40                                 Humewood-Cedarvale           0.000000   
41                     India Bazaar, The Beaches West           0.000000   
42        Kennedy Park, Ionview, East Birchmount Park           0.000000   
43          Kensington Market, Chinatown, Grange Park           0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
45                   Lawrence Manor, Lawrence Heights           0.090909   
46                                      Lawrence Park           0.000000   
47                                            Leaside           0.000000   
48                           Little Portugal, Trinity           0.000000   
49                                     Malvern, Rouge           0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...           0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...           0.000000   
52          

## Getting the top 10 venues for each neighbourhood

In [24]:
num_top_venues = 10
for neigh in toronto_grouped['Neighbourhood']:
    print("----"+neigh+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == neigh].T.reset_index()
    temp.columns = ['Venue','Frequency']
    temp = temp.iloc[1:]
    temp['Frequency'] = temp['Frequency'].astype(float)
    temp = temp.round({'Frequency': 5})
    print(temp.sort_values('Frequency', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('********************************************')
    print('\n')

----Agincourt----
                             Venue  Frequency
0                   Breakfast Spot        0.2
1                     Skating Rink        0.2
2                           Lounge        0.2
3                   Clothing Store        0.2
4        Latin American Restaurant        0.2
5                            Motel        0.0
6              Moroccan Restaurant        0.0
7              Monument / Landmark        0.0
8  Molecular Gastronomy Restaurant        0.0
9       Modern European Restaurant        0.0
********************************************


----Alderwood, Long Branch----
                      Venue  Frequency
0               Pizza Place      0.250
1                       Pub      0.125
2            Sandwich Place      0.125
3               Coffee Shop      0.125
4                       Gym      0.125
5                  Pharmacy      0.125
6                      Pool      0.125
7                      Park      0.000
8             Movie Theater      0.000
9  Medit

In [25]:
# Create a function that converts the results into a row of data that will be added to the dataframe
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [26]:
indicators = ['st', 'nd', 'rd']

columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighbourhood   1st Most Common Venue  \
0                                           Agincourt            Skating Rink   
1                              Alderwood, Long Branch             Pizza Place   
2     Bathurst Manor, Wilson Heights, Downsview North                    Bank   
3                                     Bayview Village     Japanese Restaurant   
4                   Bedford Park, Lawrence Manor East             Coffee Shop   
5                                         Berczy Park             Coffee Shop   
6                         Birch Cliff, Cliffside West         College Stadium   
7        Brockton, Parkdale Village, Exhibition Place                    Café   
8   Business reply mail Processing Centre, South C...             Yoga Studio   
9   CN Tower, King and Spadina, Railway Lands, Har...         Airport Service   
10                                Caledonia-Fairbanks                    Park   
11              Canada Post Gateway Processing Centre             Coffee Shop   
12                                          Cedarbrae             Gas Station   
13                                 Central Bay Street             Coffee Shop   
14                                           Christie           Grocery Store   
15                               Church and Wellesley             Coffee Shop   
16            Clarks Corners, Tam O'Shanter, Sullivan             Pizza Place   
17    Cliffside, Cliffcrest, Scarborough Village West                   Motel   
18                     Commerce Court, Victoria Hotel             Coffee Shop   
19                                         Davisville             Pizza Place   
20                                   Davisville North          Breakfast Spot   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn    Fast Food Restaurant   
22                                          Don Mills                     Gym   
23  Dorset Park, Wexford Heights, Scarborough Town...       Indian Restaurant   
24                                          Downsview                    Park   
25                       Dufferin, Dovercourt Village                Pharmacy   
26      East Toronto, Broadview North (Old East York)                    Park   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...             Pizza Place   
28                       Fairview, Henry Farm, Oriole          Clothing Store   
29             First Canadian Place, Underground city             Coffee Shop   
30    Forest Hill North & West, Forest Hill Road Park        Sushi Restaurant   
31                           Garden District, Ryerson             Coffee Shop   
32                                          Glencairn             Pizza Place   
33                    Golden Mile, Clairlea, Oakridge                  Bakery   
34                  Guildwood, Morningside, West Hill            Intersection   
35  Harbourfront East, Union Station, Toronto Islands             Coffee Shop   
36                      High Park, The Junction South         Thai Restaurant   
37                                  Hillcrest Village    Fast Food Restaurant   
38                                      Humber Summit             Pizza Place   
39                                   Humberlea, Emery          Baseball Field   
40                                 Humewood-Cedarvale                   Field   
41                     India Bazaar, The Beaches West                    Park   
42        Kennedy Park, Ionview, East Birchmount Park          Discount Store   
43          Kensington Market, Chinatown, Grange Park                    Café   
44  Kingsview Village, St. Phillips, Martin Grove ...          Sandwich Place   
45                   Lawrence Manor, Lawrence Heights          Clothing Store   
46                                      Lawrence Park                    Park   
47                                            Leaside             Coffee Shop   
48                           Little Portugal, Trinity                  

# Clustering
For this project we are using k-means clustering.

In [27]:
# set number of clusters
kclusters = 5

toronto_cluster = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_cluster)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([4, 1, 4, 4, 4, 4, 4, 4, 4, 4], dtype=int32)

In [28]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = torontodf

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_merged

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
5           M9A         Etobicoke   
6           M1B       Scarborough   
7           M3B        North York   
8           M4B         East York   
9           M5B  Downtown Toronto   
10          M6B        North York   
11          M9B         Etobicoke   
12          M1C       Scarborough   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
16          M6C              York   
17          M9C         Etobicoke   
18          M1E       Scarborough   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
21          M6E              York   
22          M1G       Scarborough   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
26          M1H       Scarborough   
27          M2H        North York   
28          M3H        North York   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
32          M1J       Scarborough   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
38          M1K       Scarborough   
39          M2K        North York   
40          M3K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
44          M1L       Scarborough   
45          M2L        North York   
46          M3L        North York   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
49          M6L        North York   
50          M9L        North York   
51          M1M       Scarborough   
52          M2M        North York   
53          M3M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
57          M9M        North York   
58          M1N       Scarborough   
59          M2N        North York   
60          M3N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
63          M6N              York   
64          M9N              York   
65          M1P       Scarborough   
66          M2P        North York   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
70          M9P         Etobicoke   
71          M1R       Scarborough   
72          M2R        North York   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
77          M9R         Etobicoke   
78          M1S       Scarborough   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
82          M1T       Scarborough   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
85          M1V       Scarborough   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
89          M9V         Etobicoke   
90          M1W       Scarborough   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
93          M8W         Etobicoke   
94          M9W         Etobicoke   
95          M1X       Scarborough   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
0                                            Parkwoods  43.753259 -79.32965

In [29]:
# Due to unforseen circumstances, there are NaN variables present, as a result I will drop these from the table to allow for the code to move on and convert the cluster labels to integers
toronto_merged = toronto_merged[toronto_merged['Cluster Labels'].notna()]
toronto_merged.reset_index()
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype(int)
toronto_merged

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
6           M1B       Scarborough   
7           M3B        North York   
8           M4B         East York   
9           M5B  Downtown Toronto   
10          M6B        North York   
11          M9B         Etobicoke   
12          M1C       Scarborough   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
16          M6C              York   
17          M9C         Etobicoke   
18          M1E       Scarborough   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
21          M6E              York   
22          M1G       Scarborough   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
26          M1H       Scarborough   
27          M2H        North York   
28          M3H        North York   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
32          M1J       Scarborough   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
38          M1K       Scarborough   
39          M2K        North York   
40          M3K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
44          M1L       Scarborough   
45          M2L        North York   
46          M3L        North York   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
49          M6L        North York   
50          M9L        North York   
51          M1M       Scarborough   
53          M3M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
57          M9M        North York   
58          M1N       Scarborough   
59          M2N        North York   
60          M3N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
63          M6N              York   
64          M9N              York   
65          M1P       Scarborough   
66          M2P        North York   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
70          M9P         Etobicoke   
71          M1R       Scarborough   
72          M2R        North York   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
77          M9R         Etobicoke   
78          M1S       Scarborough   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
82          M1T       Scarborough   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
85          M1V       Scarborough   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
89          M9V         Etobicoke   
90          M1W       Scarborough   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
93          M8W         Etobicoke   
94          M9W         Etobicoke   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
0                                            Parkwoods  43.753259 -79.329656   
1                                     Victoria Village  43.725882 -79.315572   
2                         

# Mapping the Clustered Data

In [30]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
rainbow = ['#000000', '#ff0000', '#0099ff', '#9c38ff', '#9e9e9e']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examining the Clusters

## Cluster 1

In [31]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0         North York               0                  Park   
21              York               0                  Park   
32       Scarborough               0            Playground   
35         East York               0                  Park   
64              York               0                  Park   
66        North York               0                  Park   
85       Scarborough               0            Playground   
91  Downtown Toronto               0                  Park   

   2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
0      Food & Drink Shop           Yoga Studio  Eastern European Restaurant   
21         Women's Store                   Bar  Eastern European Restaurant   
32         Jewelry Store   Dumpling Restaurant          Distribution Center   
35         Metro Station     Convenience Store            Electronics Store   
64         Jewelry Store     Convenience Store                  Yoga Studio   
66     Convenience Store           Yoga Studio            Electronics Store   
85                  Park          Intersection                 Concert Hall   
91            Playground                 Trail                  Yoga Studio   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                       Dog Run      Doner Restaurant            Donut Shop   
21                      Dog Run      Doner Restaurant            Donut Shop   
32                      Dog Run      Doner Restaurant            Donut Shop   
35                      Dog Run      Doner Restaurant            Donut Shop   
64  Eastern European Restaurant               Dog Run      Doner Restaurant   
66                      Dog Run      Doner Restaurant            Donut Shop   
85                   Comic Shop        Farmers Market    Falafel Restaurant   
91                    Drugstore        Discount Store   Distribution Center   

   8th Most Common Venue        9th Most Common Venue  \
0              Drugstore          Dumpling Restaurant   
21             Drugstore          Dumpling Restaurant   
32             Drugstore  Eastern European Restaurant   
35             Drugstore          Dumpling Restaurant   
64            Donut Shop                    Drugstore   
66             Drugstore          Dumpling Restaurant   
85           Event Space         Ethiopian Restaurant   
91               Dog Run             Doner Restaurant   

         10th Most Common Venue  
0                   Escape Room  
21            Electronics Store  
32                        Field  
35  Eastern European Restaurant  
64          Dumpling Restaurant  
66  Eastern European Restaurant  
85                  Escape Room  
91                   Donut Shop

## Cluster 2

In [32]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
6   Scarborough               1  Fast Food Restaurant           Yoga Studio   
50   North York               1           Pizza Place           Yoga Studio   
56         York               1  Fast Food Restaurant        Sandwich Place   
63         York               1           Pizza Place               Brewery   
72   North York               1           Pizza Place         Grocery Store   
82  Scarborough               1           Pizza Place           Gas Station   
89    Etobicoke               1           Pizza Place         Grocery Store   
93    Etobicoke               1           Pizza Place                  Pool   

          3rd Most Common Venue 4th Most Common Venue  \
6   Eastern European Restaurant   Distribution Center   
50  Eastern European Restaurant   Distribution Center   
56               Discount Store   Fried Chicken Joint   
63            Convenience Store         Grocery Store   
72                      Butcher           Coffee Shop   
82                 Noodle House    Chinese Restaurant   
89                  Video Store        Sandwich Place   
93                          Pub           Coffee Shop   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
6                       Dog Run      Doner Restaurant            Donut Shop   
50                      Dog Run      Doner Restaurant            Donut Shop   
56                   Restaurant            Donut Shop   Distribution Center   
63  Eastern European Restaurant               Dog Run      Doner Restaurant   
72                     Pharmacy          Concert Hall        Discount Store   
82         Fast Food Restaurant   Fried Chicken Joint                  Bank   
89         Fast Food Restaurant            Beer Store   Fried Chicken Joint   
93                          Gym              Pharmacy        Sandwich Place   

   8th Most Common Venue 9th Most Common Venue       10th Most Common Venue  
6              Drugstore   Dumpling Restaurant            Electronics Store  
50             Drugstore   Dumpling Restaurant            Electronics Store  
56               Dog Run      Doner Restaurant                  Yoga Studio  
63            Donut Shop             Drugstore          Dumpling Restaurant  
72    Falafel Restaurant           Event Space         Ethiopian Restaurant  
82    Italian Restaurant          Intersection              Thai Restaurant  
89              Pharmacy           Golf Course             Department Store  
93           Escape Room     Electronics Store  Eastern European Restaurant

## Cluster 3

In [33]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
57   North York               2        Baseball Field           Yoga Studio   
101   Etobicoke               2        Breakfast Spot      Business Service   

           3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
57   Eastern European Restaurant               Dog Run      Doner Restaurant   
101               Baseball Field           Yoga Studio     Electronics Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
57             Donut Shop             Drugstore   Dumpling Restaurant   
101            Donut Shop             Drugstore   Dumpling Restaurant   

           9th Most Common Venue 10th Most Common Venue  
57             Electronics Store    Filipino Restaurant  
101  Eastern European Restaurant            Escape Room

## Cluster 4

In [34]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
11  Etobicoke               3   Filipino Restaurant   

          2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
11  Eastern European Restaurant   Distribution Center               Dog Run   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
11      Doner Restaurant            Donut Shop             Drugstore   

   8th Most Common Venue 9th Most Common Venue   10th Most Common Venue  
11   Dumpling Restaurant     Electronics Store  Health & Beauty Service

## Cluster 5

In [35]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels   1st Most Common Venue  \
1          North York               4             Pizza Place   
2    Downtown Toronto               4             Coffee Shop   
3          North York               4          Clothing Store   
4    Downtown Toronto               4             Coffee Shop   
7          North York               4                     Gym   
8           East York               4             Pizza Place   
9    Downtown Toronto               4             Coffee Shop   
10         North York               4             Pizza Place   
12        Scarborough               4                     Bar   
13         North York               4                     Gym   
14          East York               4            Skating Rink   
15   Downtown Toronto               4             Coffee Shop   
16               York               4                   Field   
17          Etobicoke               4             Pizza Place   
18        Scarborough               4            Intersection   
19       East Toronto               4       Health Food Store   
20   Downtown Toronto               4             Coffee Shop   
22        Scarborough               4             Coffee Shop   
23          East York               4             Coffee Shop   
24   Downtown Toronto               4             Coffee Shop   
25   Downtown Toronto               4           Grocery Store   
26        Scarborough               4             Gas Station   
27         North York               4    Fast Food Restaurant   
28         North York               4                    Bank   
29          East York               4       Indian Restaurant   
30   Downtown Toronto               4             Coffee Shop   
31       West Toronto               4                Pharmacy   
33         North York               4          Clothing Store   
34         North York               4  Furniture / Home Store   
36   Downtown Toronto               4             Coffee Shop   
37       West Toronto               4                     Bar   
38        Scarborough               4          Discount Store   
39         North York               4     Japanese Restaurant   
40         North York               4                    Park   
41       East Toronto               4        Greek Restaurant   
42   Downtown Toronto               4             Coffee Shop   
43       West Toronto               4                    Café   
44        Scarborough               4                  Bakery   
45         North York               4     Martial Arts School   
46         North York               4                    Park   
47       East Toronto               4                    Park   
48   Downtown Toronto               4             Coffee Shop   
49         North York               4                  Bakery   
51        Scarborough               4                   Motel   
53         North York               4                    Park   
54       East Toronto               4             Coffee Shop   
55         North York               4             Coffee Shop   
58        Scarborough               4         College Stadium   
59         North York               4        Ramen Restaurant   
60         North York               4                    Park   
61    Central Toronto               4                    Park   
62    Central Toronto               4                  Garden   
65        Scarborough               4       Indian Restaurant   
67    Central Toronto               4          Breakfast Spot   
68    Central Toronto               4        Sushi Restaurant   
69       West Toronto               4         Thai Restaurant   
70          Etobicoke               4             Pizza Place   
71        Scarborough               4                  Bakery   
73    Central Toronto               4     Sporting Goods Shop   
74    Central Toronto               4          Sandwich Place   
75       West Toronto               4          Br

# In-Depth Analysis

In this section we combine the 10 neighbourhoods with the population and income data and combine it with the respective most common venues

In [36]:
finaldf = indepthdf.merge(toronto_merged, on='Neighbourhood', how='left')
finaldf

Postal Code_x     Borough_x        Neighbourhood  Latitude_x  Longitude_x  \
0           M4A    North York     Victoria Village   43.725882   -79.315572   
1           M6C          York   Humewood-Cedarvale   43.693781   -79.428191   
2           M4E  East Toronto          The Beaches   43.676357   -79.293031   
3           M1G   Scarborough               Woburn   43.770992   -79.216917   
4           M2H    North York    Hillcrest Village   43.803762   -79.363452   
5           M4H     East York     Thorncliffe Park   43.705369   -79.349372   
6           M1J   Scarborough  Scarborough Village   43.744734   -79.239476   
7           M2K    North York      Bayview Village   43.786947   -79.385975   
8           M9L    North York        Humber Summit   43.756303   -79.565963   
9           M9N          York               Weston   43.706876   -79.518188   

  Population Average Income Postal Code_y     Borough_y  Latitude_y  \
0     17,510         35,786           M4A    North York   43.725882   
1     14,365         65,274           M6C          York   43.693781   
2     21,567         92,580           M4E  East Toronto   43.676357   
3     53,485         30,878           M1G   Scarborough   43.770992   
4     16,934         40,442           M2H    North York   43.803762   
5     21,108         28,875           M4H     East York   43.705369   
6     16,724         32,913           M1J   Scarborough   43.744734   
7     21,396         52,035           M2K    North York   43.786947   
8     12,416         30,731           M9L    North York   43.756303   
9     17,992         32,997           M9N          York   43.706876   

   Longitude_y  Cluster Labels 1st Most Common Venue  2nd Most Common Venue  \
0   -79.315572               4           Pizza Place           Hockey Arena   
1   -79.428191               4                 Field                Dog Run   
2   -79.293031               4     Health Food Store           Neighborhood   
3   -79.216917               4           Coffee Shop  Korean BBQ Restaurant   
4   -79.363452               4  Fast Food Restaurant                Dog Run   
5   -79.349372               4     Indian Restaurant         Sandwich Place   
6   -79.239476               0            Playground          Jewelry Store   
7   -79.385975               4   Japanese Restaurant                   Bank   
8   -79.565963               1           Pizza Place            Yoga Studio   
9   -79.518188               0                  Park          Jewelry Store   

         3rd Most Common Venue        4th Most Common Venue  \
0                 Intersection            French Restaurant   
1                 Hockey Arena                        Trail   
2                        Trail                          Pub   
3                  Yoga Studio  Eastern European Restaurant   
4                         Pool     Mediterranean Restaurant   
5                  Yoga Studio                         Bank   
6          Dumpling Restaurant          Distribution Center   
7           Chinese Restaurant                         Café   
8  Eastern European Restaurant          Distribution Center   
9            Convenience Store                  Yoga Studio   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Portuguese Restaurant           Coffee Shop     Electronics Store   
1                  Yoga Studio   Dumpling Restaurant   Distribution Center   
2                    Drugstore        Discount Store   Distribution Center   
3                      Dog Run      Doner Restaurant            Donut Shop   
4           Athletics & Sports           Golf Course           Yoga Studio   
5                Grocery Store           Gas Station  Fast Food Restaurant   
6                      Dog Run      Doner Restaurant            Donut Shop   
7                  Yoga Studio      Doner Restaurant            Donut Shop   
8                      Dog Run      Doner Restaurant            Donut Shop   
9  Eas

In [37]:
# drop the repeated columns
finaldf = finaldf.drop(columns=['Postal Code_y', 'Borough_y', 'Latitude_y', 'Longitude_y'])
finaldf

Postal Code_x     Borough_x        Neighbourhood  Latitude_x  Longitude_x  \
0           M4A    North York     Victoria Village   43.725882   -79.315572   
1           M6C          York   Humewood-Cedarvale   43.693781   -79.428191   
2           M4E  East Toronto          The Beaches   43.676357   -79.293031   
3           M1G   Scarborough               Woburn   43.770992   -79.216917   
4           M2H    North York    Hillcrest Village   43.803762   -79.363452   
5           M4H     East York     Thorncliffe Park   43.705369   -79.349372   
6           M1J   Scarborough  Scarborough Village   43.744734   -79.239476   
7           M2K    North York      Bayview Village   43.786947   -79.385975   
8           M9L    North York        Humber Summit   43.756303   -79.565963   
9           M9N          York               Weston   43.706876   -79.518188   

  Population Average Income  Cluster Labels 1st Most Common Venue  \
0     17,510         35,786               4           Pizza Place   
1     14,365         65,274               4                 Field   
2     21,567         92,580               4     Health Food Store   
3     53,485         30,878               4           Coffee Shop   
4     16,934         40,442               4  Fast Food Restaurant   
5     21,108         28,875               4     Indian Restaurant   
6     16,724         32,913               0            Playground   
7     21,396         52,035               4   Japanese Restaurant   
8     12,416         30,731               1           Pizza Place   
9     17,992         32,997               0                  Park   

   2nd Most Common Venue        3rd Most Common Venue  \
0           Hockey Arena                 Intersection   
1                Dog Run                 Hockey Arena   
2           Neighborhood                        Trail   
3  Korean BBQ Restaurant                  Yoga Studio   
4                Dog Run                         Pool   
5         Sandwich Place                  Yoga Studio   
6          Jewelry Store          Dumpling Restaurant   
7                   Bank           Chinese Restaurant   
8            Yoga Studio  Eastern European Restaurant   
9          Jewelry Store            Convenience Store   

         4th Most Common Venue        5th Most Common Venue  \
0            French Restaurant        Portuguese Restaurant   
1                        Trail                  Yoga Studio   
2                          Pub                    Drugstore   
3  Eastern European Restaurant                      Dog Run   
4     Mediterranean Restaurant           Athletics & Sports   
5                         Bank                Grocery Store   
6          Distribution Center                      Dog Run   
7                         Café                  Yoga Studio   
8          Distribution Center                      Dog Run   
9                  Yoga Studio  Eastern European Restaurant   

  6th Most Common Venue 7th Most Common Venue      8th Most Common Venue  \
0           Coffee Shop     Electronics Store                Escape Room   
1   Dumpling Restaurant   Distribution Center           Doner Restaurant   
2        Discount Store   Distribution Center                    Dog Run   
3      Doner Restaurant            Donut Shop                  Drugstore   
4           Golf Course           Yoga Studio        Dumpling Restaurant   
5           Gas Station  Fast Food Restaurant  Middle Eastern Restaurant   
6      Doner Restaurant            Donut Shop                  Drugstore   
7      Doner Restaurant            Donut Shop                  Drugstore   
8      Doner Restaurant            Donut Shop                  Drugstore   
9               Dog Run      Doner Restaurant                 Donut Shop   

         9th Most Common Venue       10th Most Common Venue  
0  Eastern European Restaurant          Dumpling Restaurant  
1                   Donut Shop                    Drugstore  
2             Doner Restaur

## Mapping out the 10 neighbourhoods to see their locations

In [38]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
rainbow = ['#000000', '#ff0000', '#0099ff', '#9c38ff', '#9e9e9e']

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(finaldf['Latitude_x'], finaldf['Longitude_x'], finaldf['Neighbourhood'], finaldf['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Thank you!